# Description

Each thread (1,2,4)
* Each ends by pushing to a differnt MongoDB Collection
* Thread 4 retains state in memory

Thread 0 (Initialize plots, master thread)

Thread 1 (Collect Raw Data)

Thread 2 (Aggregate capped collection)

Thread 3 - GUI output (Update plots from processed data)

Thread 4 - GUI input (Manage Experimental state, Save timestamps, state_info, and experiment_info)
* Maybe MongoDB to save collection of experiments with an experiment id that can be linked to the experimental state timestamping

In [8]:
import pymongo
from datetime import datetime
client = pymongo.MongoClient()
db = client.test_database
experiment_timestamps = db["experiment_timestamps"]
#events = db["events"]
#dateTimeObj3 = datetime.now()
#timeStr3 = dateTimeObj3.strftime("%Y-%m-%d %H:%M:%S.%f")
#db.events.insert_one({'t':timeStr3, 'describe':'initiate collection'})
#db.create_collection('temp0', capped=True, max=1, size=1000)
#db.create_collection('temp1', capped=True, max=1, size=1000)
#db.create_collection('temp2', capped=True, max=1, size=1000)
#db.create_collection('temp3', capped=True, max=1, size=1000)
"""
processed_1 = db["processed_1"]
db.processed_1.insert_one({'t':timeStr3, 'complex_wavelet_matrix':0,
                          'Hjorth_A':0, 'Hjorth_M':0, 'Hjorth_C':0})
processed_2 = db["processed_2"]
db.processed_2.insert_one({'t':timeStr3, 'complex_wavelet_matrix':0,
                          'Hjorth_A':0, 'Hjorth_M':0, 'Hjorth_C':0})
processed_3 = db["processed_3"]
db.processed_3.insert_one({'t':timeStr3, 'complex_wavelet_matrix':0,
                          'Hjorth_A':0, 'Hjorth_M':0, 'Hjorth_C':0})
"""

db.collection_names()

['test_capped2',
 'temp1',
 'processed_2',
 'temp3',
 'temp',
 'test_capped',
 'raw_cappedCollection_65',
 'events',
 'temp2',
 'processed_1',
 'temp0',
 'posts',
 'processed_3',
 'test_capped3',
 'processed_0']

# Main deal

In [1]:
# Thread 0 (master thread)

%matplotlib widget

from time import time, sleep
from threading import *

import numpy as np
import matplotlib
matplotlib.rcParams['font.size'] = 11
import matplotlib.pyplot as plt
import pandas as pd
import pymongo

client = pymongo.MongoClient()
db = client.test_database
#db.list_collection_names

import ipywidgets

from datetime import datetime





# Complex morlet wavelets (cmw) consist of a sine wave multiplied by a Gaussian. 
# (The imaginary term comes from Euler's formula.)
cmw = lambda t, f, s: (1/np.sqrt(s*np.sqrt(np.pi))) * np.exp(-t**2/(2*s**2)) * np.exp(1j*2*np.pi*f*t)
# Where t is time axis, f is peak frequency of wavelet, and s is standard deviation of Gaussian (std_for_gaussian)
std_for_gaussian = lambda n, f: n/(2*np.pi*f)
# Where f is peak frequency of wavelet and n is number of wavelet cycles
wavelet_x = np.linspace(-.25/2, .25/2, 65)
complex_morlet_wavelet = cmw(wavelet_x, f=10, s=std_for_gaussian(n=10, f=10))



def eeg_handler(address: str,*args):
            dateTimeObj = datetime.now()
            printStr = dateTimeObj.strftime("%Y-%m-%d %H:%M:%S.%f")
            data_dict = {"t":printStr, "TP9":float(args[0]), "AF7":float(args[1]), "AF8":float(args[2]), "TP10":float(args[3])}
            db.raw_cappedCollection_65.insert_one(data_dict)

# Start threads
class thread1(Thread):
    def run(self):
        from pythonosc import dispatcher
        from pythonosc import osc_server
        ip = "192.168.1.165"
        port = 5000

        if __name__ == "__main__":
            dispatcher = dispatcher.Dispatcher()
            dispatcher.map("/muse/eeg", eeg_handler)
            server = osc_server.ThreadingOSCUDPServer((ip, port), dispatcher)
            print("Listening on UDP port "+str(port))
            server.serve_forever()

class thread2(Thread):
    def run(self):
        self.running=True
        while self.running==True:
            # Thread 2 (Aggregate capped collection)
            timeit = time()
            docs = db.raw_cappedCollection_65.find({}, projection={"TP9":1, "AF7":1, "AF8":1, "TP10":1, "_id":0})
            X = np.array([[doc['TP9'], doc['AF7'], doc['AF8'], doc['TP10']] for doc in docs])
            wavelet_solution = np.dot(complex_morlet_wavelet, X)   # Convolution-like operation. Shape=(n_wavelets, n_channels)
            wavelet_solution = np.abs(wavelet_solution**2)
            #print("wavelet_solution.shape",wavelet_solution.shape)
            Hjorth_parameters = {'A': np.var(X, axis=0), 
                                 'M': np.sqrt(np.var(np.diff(X, axis=0), axis=0)/np.var(X, axis=0)),
                                 'C': np.sqrt(np.var(np.diff(X, n=2, axis=0), axis=0)/np.var(X, axis=0))}

            #list_wavelet_solutions.append(wavelet_solution)
            #list_Hjorth_parameters.append(Hjorth_parameters)
            
            dateTimeObj2 = datetime.now()
            global timeStr
            timeStr = dateTimeObj2.strftime("%Y-%m-%d %H:%M:%S.%f")

            processed_data_dict0 = {'t':timeStr, 
                                  'complex_wavelet_matrix':wavelet_solution[0], 
                                  'Hjorth_A':Hjorth_parameters['A'][0],
                                  'Hjorth_M':Hjorth_parameters['M'][0],
                                  'Hjorth_C':Hjorth_parameters['C'][0]}  
            processed_data_dict1 = {'t':timeStr, 
                                  'complex_wavelet_matrix':wavelet_solution[1], 
                                  'Hjorth_A':Hjorth_parameters['A'][1],
                                  'Hjorth_M':Hjorth_parameters['M'][1],
                                  'Hjorth_C':Hjorth_parameters['C'][1]} 
            processed_data_dict2 = {'t':timeStr, 
                                  'complex_wavelet_matrix':wavelet_solution[2], 
                                  'Hjorth_A':Hjorth_parameters['A'][2],
                                  'Hjorth_M':Hjorth_parameters['M'][2],
                                  'Hjorth_C':Hjorth_parameters['C'][2]} 
            processed_data_dict3 = {'t':timeStr, 
                                  'complex_wavelet_matrix':wavelet_solution[3], 
                                  'Hjorth_A':Hjorth_parameters['A'][3],
                                  'Hjorth_M':Hjorth_parameters['M'][3],
                                  'Hjorth_C':Hjorth_parameters['C'][3]} 

            db.processed_0.insert_one(processed_data_dict0)
            db.processed_1.insert_one(processed_data_dict1)
            db.processed_2.insert_one(processed_data_dict2)
            db.processed_3.insert_one(processed_data_dict3)
            db.temp0.insert_one(processed_data_dict0)
            db.temp1.insert_one(processed_data_dict1)
            db.temp2.insert_one(processed_data_dict2)
            db.temp3.insert_one(processed_data_dict3)
            
            
            sleep(0.1)

class thread3(Thread):
    def run(self):
        self.running=True
        while self.running==True:
            timeit = time()
            for lines, collection, x_adjust in zip([lines0, lines1, lines2, lines3], 
                                         ['temp0', 'temp1', 'temp2', 'temp3'], [-0.15, -0.05, 0.05, 0.15]):
                change = db[collection].find_one()
                lines[0].set_data(x+x_adjust, [np.sqrt(change['complex_wavelet_matrix']), change['Hjorth_A'], change['Hjorth_M'], change['Hjorth_C']])
            fig.canvas.draw()
            fig.canvas.flush_events()
            sleep(0.1)
            
plt.ioff()

#from IPython.display import display
button = ipywidgets.Button(description="Quit")
output = ipywidgets.Output()


def on_button_clicked(b):
    with output:
        print("Quit button clicked")
        t2.running = False
        t3.running = False

button.on_click(on_button_clicked)

button.layout.margin = '0px 40% 0px 40%'
button.layout.width = '20%'

#display(button, output)




fig = plt.figure(figsize=[10,4])
fig.canvas.header_visible = False
fig.canvas.layout.min_height = '400px'
plt.title('Plotting features')
x = np.array([0,1,2,3])
lines0 = plt.plot(x-0.15, [1,1,1,1], marker='x', ls='')
lines1 = plt.plot(x-0.05, [1,1,1,1], marker='x', ls='')
lines2 = plt.plot(x+0.05, [1,1,1,1], marker='x', ls='')
lines3 = plt.plot(x+0.15, [1,1,1,1], marker='x', ls='')
plt.xticks(ticks=[0,1,2,3], labels=['10Hz wavelet', 'Hjorth_A', 'Hjorth_M', 'Hjorth_C'])
plt.yscale('log')
plt.ylim(0.01, 100000)
plt.xlim(-0.5, 3.5)
plt.legend(['tp9', 'af7', 'af8', 'tp10'], loc='upper right')


t1 = thread1()
t2 = thread2()
t3 = thread3()

t1.start()
sleep(0.25)
t2.start()
sleep(0.05)
t3.start()

ipywidgets.AppLayout(
    center=fig.canvas,
    header=button,
    footer=output,
    pane_heights=[0, 6, 1],
    pane_widths=[10,10,10]
    
)

# ideas - 

Listening on UDP port 5000


AppLayout(children=(Button(description='Quit', layout=Layout(grid_area='header', margin='0px 40% 0px 40%', wid…

In [4]:
%matplotlib widget

Using matplotlib backend: module://ipympl.backend_nbagg


# June 16 - Iteration 2

In [1]:
# Thread 0 (master thread)

%matplotlib widget

from time import time, sleep
from threading import *

import numpy as np
import matplotlib
matplotlib.rcParams['font.size'] = 11
import matplotlib.pyplot as plt
import pandas as pd
import pymongo

client = pymongo.MongoClient()
db = client.test_database
#db.list_collection_names

import ipywidgets
import datetime





# Complex morlet wavelets (cmw) consist of a sine wave multiplied by a Gaussian. 
# (The imaginary term comes from Euler's formula.)
cmw = lambda t, f, s: (1/np.sqrt(s*np.sqrt(np.pi))) * np.exp(-t**2/(2*s**2)) * np.exp(1j*2*np.pi*f*t)
# Where t is time axis, f is peak frequency of wavelet, and s is standard deviation of Gaussian (std_for_gaussian)
std_for_gaussian = lambda n, f: n/(2*np.pi*f)
# Where f is peak frequency of wavelet and n is number of wavelet cycles
wavelet_x = np.linspace(-.25/2, .25/2, 65)
complex_morlet_wavelet = cmw(wavelet_x, f=10, s=std_for_gaussian(n=10, f=10))



def eeg_handler(address: str,*args):
            dateTimeObj = datetime.datetime.now()
            printStr = dateTimeObj.strftime("%Y-%m-%d %H:%M:%S.%f")
            data_dict = {"t":printStr, "TP9":float(args[0]), "AF7":float(args[1]), "AF8":float(args[2]), "TP10":float(args[3])}
            db.raw_cappedCollection_65.insert_one(data_dict)

# Start threads
class EEG_Server(Thread):
    def run(self):
        from pythonosc import dispatcher
        from pythonosc import osc_server
        ip = "192.168.1.165"
        port = 5000

        if __name__ == "__main__":
            dispatcher = dispatcher.Dispatcher()
            dispatcher.map("/muse/eeg", eeg_handler)
            server = osc_server.ThreadingOSCUDPServer((ip, port), dispatcher)
            print("Listening on UDP port "+str(port))
            server.serve_forever()

class Aggregator(Thread):
    def run(self):
        self.running=True
        while self.running==True:
            # Thread 2 (Aggregate capped collection)
            timeit = time()
            docs = db.raw_cappedCollection_65.find({}, projection={"TP9":1, "AF7":1, "AF8":1, "TP10":1, "_id":0})
            X = np.array([[doc['TP9'], doc['AF7'], doc['AF8'], doc['TP10']] for doc in docs])
            wavelet_solution = np.dot(complex_morlet_wavelet, X)   # Convolution-like operation. Shape=(n_wavelets, n_channels)
            wavelet_solution = np.abs(wavelet_solution**2)
            #print("wavelet_solution.shape",wavelet_solution.shape)
            Hjorth_parameters = {'A': np.var(X, axis=0), 
                                 'M': np.sqrt(np.var(np.diff(X, axis=0), axis=0)/np.var(X, axis=0)),
                                 'C': np.sqrt(np.var(np.diff(X, n=2, axis=0), axis=0)/np.var(X, axis=0))}

            #list_wavelet_solutions.append(wavelet_solution)
            #list_Hjorth_parameters.append(Hjorth_parameters)
            
            dateTimeObj2 = datetime.datetime.now()
            global timeStr
            timeStr = dateTimeObj2.strftime("%Y-%m-%d %H:%M:%S.%f")

            processed_data_dict0 = {'t':timeStr, 
                                  'complex_wavelet_matrix':wavelet_solution[0], 
                                  'Hjorth_A':Hjorth_parameters['A'][0],
                                  'Hjorth_M':Hjorth_parameters['M'][0],
                                  'Hjorth_C':Hjorth_parameters['C'][0]}  
            processed_data_dict1 = {'t':timeStr, 
                                  'complex_wavelet_matrix':wavelet_solution[1], 
                                  'Hjorth_A':Hjorth_parameters['A'][1],
                                  'Hjorth_M':Hjorth_parameters['M'][1],
                                  'Hjorth_C':Hjorth_parameters['C'][1]} 
            processed_data_dict2 = {'t':timeStr, 
                                  'complex_wavelet_matrix':wavelet_solution[2], 
                                  'Hjorth_A':Hjorth_parameters['A'][2],
                                  'Hjorth_M':Hjorth_parameters['M'][2],
                                  'Hjorth_C':Hjorth_parameters['C'][2]} 
            processed_data_dict3 = {'t':timeStr, 
                                  'complex_wavelet_matrix':wavelet_solution[3], 
                                  'Hjorth_A':Hjorth_parameters['A'][3],
                                  'Hjorth_M':Hjorth_parameters['M'][3],
                                  'Hjorth_C':Hjorth_parameters['C'][3]} 

            db.processed_0.insert_one(processed_data_dict0)
            db.processed_1.insert_one(processed_data_dict1)
            db.processed_2.insert_one(processed_data_dict2)
            db.processed_3.insert_one(processed_data_dict3)
            db.temp0.insert_one(processed_data_dict0)
            db.temp1.insert_one(processed_data_dict1)
            db.temp2.insert_one(processed_data_dict2)
            db.temp3.insert_one(processed_data_dict3)
            
            
            sleep(0.1)

class Plotter(Thread):
    """Input from MongoDB Collection = db.temp0 and db.temp1 and db.temp2 and db.temp3"""
    def run(self):
        self.running=True
        while self.running==True:
            timeit = time()
            for lines, collection, x_adjust in zip([lines0, lines1, lines2, lines3], 
                                         ['temp0', 'temp1', 'temp2', 'temp3'], [-0.15, -0.05, 0.05, 0.15]):
                change = db[collection].find_one()
                lines[0].set_data(x+x_adjust, [np.sqrt(change['complex_wavelet_matrix']), 
                                               change['Hjorth_A'], change['Hjorth_M'], change['Hjorth_C']])
            fig.canvas.draw()
            fig.canvas.flush_events()
            sleep(0.1)
            
class Experiment_Handler(Thread):
    """Output to MongoDB Collection = db.experiment_timestamps"""
    def __init__(self, textarea_value):
        self.textarea_value = textarea_value
    def run(self):
        self.running=True
        while self.running==True:
            exp_id = self.textarea_value.split(')')[0]
            items_from_param_dict = self.textarea_value.split(')')[1].split(',')
            seconds_from_param_dict = [int(item.split(':')[0]) for item in items_from_param_dict]
            names_from_param_dict = [str(item.split(':')[1]) for item in items_from_param_dict]
            self.time0 = datetime.datetime.now()
            self.previous_second = datetime.timedelta(seconds=0)
            for second, name in zip(seconds_from_param_dict, names_from_param_dict):
                time_nextState = self.time0 + datetime.timedelta(seconds=second)
                
                while datetime.datetime.now() < time_nextState:
                    sleep(0.1)
                    self.current_second = datetime.datetime.now() - self.time0
                    if (self.current_second - self.previous_second) > datetime.timedelta(seconds=1):
                        with output2:
                            print(self.current_second)
                            self.previous_second = self.current_second
                db.experiment_timestamps.insert_one({'t':time_nextState, 'new_state': name, 'experiment_id':exp_id})
            self.running=False
                
            ####################################
            
plt.ioff()

#from IPython.display import display
button = ipywidgets.Button(description="Quit")
output = ipywidgets.Output()
output2 = ipywidgets.Output()


def on_button_clicked(b):
    with output:
        print("Quit button clicked")
        t2.running = False
        t3.running = False

button.on_click(on_button_clicked)

button.layout.margin = '0px 40% 0px 40%'
button.layout.width = '20%'



#display(button, output)




fig = plt.figure(figsize=[10,4])
fig.canvas.header_visible = False
fig.canvas.layout.min_height = '400px'
plt.title('Plotting features')
x = np.array([0,1,2,3])
lines0 = plt.plot(x-0.15, [1,1,1,1], marker='x', ls='')
lines1 = plt.plot(x-0.05, [1,1,1,1], marker='x', ls='')
lines2 = plt.plot(x+0.05, [1,1,1,1], marker='x', ls='')
lines3 = plt.plot(x+0.15, [1,1,1,1], marker='x', ls='')
plt.xticks(ticks=[0,1,2,3], labels=['10Hz wavelet', 'Hjorth_A', 'Hjorth_M', 'Hjorth_C'])
plt.yscale('log')
plt.ylim(0.01, 100000)
plt.xlim(-0.5, 3.5)
plt.legend(['tp9', 'af7', 'af8', 'tp10'], loc='upper right')


# Experimental framework
exp_params_textarea = ipywidgets.Textarea(
    value='',
    placeholder='EXP_ID)integer:\"string\", integer:\"string\", ...:...',
    description='Experiment protocol - {seconds:new_state,}'
    )
exec_button = ipywidgets.Button(description="Begin")

def exec_button_clicked(b):
    """Begin experiment according to parameter dictionary"""
    with output2:
        t4 = Experiment_Handler(textarea_value=exp_params_textarea.value)
        t4.run()
        sleep(0.1)
        while t4.running==True:
            print(datetime.datetime.now() - t4.time0)
            sleep(1)
        print('EXPERIMENT COMPLETE')

exec_button.on_click(exec_button_clicked)

TwoByTwoFooter = ipywidgets.TwoByTwoLayout(top_left=exp_params_textarea, 
                          top_right=exec_button, bottom_left=output, bottom_right=output2)


t1 = EEG_Server()
t2 = Aggregator()
t3 = Plotter()

t1.start()
sleep(0.25)
t2.start()
sleep(0.05)
t3.start()

ipywidgets.AppLayout(
    center=fig.canvas,
    header=button,
    footer=TwoByTwoFooter,
    pane_heights=[1, 10, 10],
)

# ideas - 
# Experimental framework must assign... timestamps (datetime), 
# experiment segment labels (dictionary?) [segment int label with text to display]
# Experiment ID

# retrieve collection aggregated data according to timestamps
# automatically plot and do crude statistics

Listening on UDP port 5000


AppLayout(children=(Button(description='Quit', layout=Layout(grid_area='header', margin='0px 40% 0px 40%', wid…

In [7]:
Plotter

NameError: name 'Plotter' is not defined

In [2]:
db.collection_names()

['test_capped2',
 'temp1',
 'processed_2',
 'temp3',
 'temp',
 'test_capped',
 'raw_cappedCollection_65',
 'events',
 'temp2',
 'processed_1',
 'temp0',
 'experiment_timestamps',
 'posts',
 'processed_3',
 'test_capped3',
 'processed_0']

In [2]:
docs = db.experiment_timestamps.find()
for doc in docs:
    print(doc)

{'_id': ObjectId('60ca4ad3d64ad43994984311'), 't': datetime.datetime(2021, 6, 16, 15, 2, 43, 726000), 'new_state': 'Normal', 'experiment_id': '1'}
{'_id': ObjectId('60ca4ad7d64ad439949846f6'), 't': datetime.datetime(2021, 6, 16, 15, 2, 47, 726000), 'new_state': 'Chew', 'experiment_id': '1'}
{'_id': ObjectId('60ca4adbd64ad43994984afd'), 't': datetime.datetime(2021, 6, 16, 15, 2, 51, 726000), 'new_state': 'End', 'experiment_id': '1'}
{'_id': ObjectId('60ca4adcd64ad43994984c44'), 't': datetime.datetime(2021, 6, 16, 15, 2, 52, 898000), 'new_state': 'Normal', 'experiment_id': '1'}
{'_id': ObjectId('60ca4ae0d64ad4399498502c'), 't': datetime.datetime(2021, 6, 16, 15, 2, 56, 898000), 'new_state': 'Chew', 'experiment_id': '1'}
{'_id': ObjectId('60ca4ae4d64ad43994985430'), 't': datetime.datetime(2021, 6, 16, 15, 3, 0, 898000), 'new_state': 'End', 'experiment_id': '1'}
{'_id': ObjectId('60ca55ded64ad42c58b9026a'), 't': datetime.datetime(2021, 6, 16, 15, 49, 50, 340000), 'new_state': 'Normal', 'ex

In [3]:
docs = db.processed_0.find()
for doc in docs:
    print(doc)

{'_id': ObjectId('60c90c97d64ad446fc90255f'), 't': '2021-06-15 16:24:55.241628', 'complex_wavelet_matrix': 81725835.61141752, 'Hjorth_A': 80.7424030126869, 'Hjorth_M': 0.8657034634388128, 'Hjorth_C': 1.1371894727453067}
{'_id': ObjectId('60c90c97d64ad446fc902562'), 't': '2021-06-15 16:24:55.727667', 'complex_wavelet_matrix': 82527447.18360469, 'Hjorth_A': 81.32689002666422, 'Hjorth_M': 0.8710044253584807, 'Hjorth_C': 1.1630386662295435}
{'_id': ObjectId('60c90c98d64ad446fc902565'), 't': '2021-06-15 16:24:56.200702', 'complex_wavelet_matrix': 82477568.31379855, 'Hjorth_A': 84.77760615947155, 'Hjorth_M': 0.866255371357848, 'Hjorth_C': 1.1481871102203633}
{'_id': ObjectId('60c90c98d64ad446fc90256b'), 't': '2021-06-15 16:24:56.546727', 'complex_wavelet_matrix': 79185110.78773433, 'Hjorth_A': 111.46417273408736, 'Hjorth_M': 0.7892115352457995, 'Hjorth_C': 1.0259816435385376}
{'_id': ObjectId('60c90c99d64ad446fc902572'), 't': '2021-06-15 16:24:57.097768', 'complex_wavelet_matrix': 76124530.2

{'_id': ObjectId('60c90cb8d64ad446fc903beb'), 't': '2021-06-15 16:25:28.384977', 'complex_wavelet_matrix': 78054654.2293855, 'Hjorth_A': 41.622635543334034, 'Hjorth_M': 0.864091494822691, 'Hjorth_C': 1.1724166493478096}
{'_id': ObjectId('60c90cb8d64ad446fc903c40'), 't': '2021-06-15 16:25:28.653216', 'complex_wavelet_matrix': 82255980.68208504, 'Hjorth_A': 46.14879908468597, 'Hjorth_M': 0.8056317051081012, 'Hjorth_C': 1.0727888147094016}
{'_id': ObjectId('60c90cb8d64ad446fc903c7d'), 't': '2021-06-15 16:25:28.912930', 'complex_wavelet_matrix': 82462673.13624582, 'Hjorth_A': 63.10722853265391, 'Hjorth_M': 0.7281514294754208, 'Hjorth_C': 0.9760467233098117}
{'_id': ObjectId('60c90cb9d64ad446fc903cba'), 't': '2021-06-15 16:25:29.178675', 'complex_wavelet_matrix': 77028856.19165103, 'Hjorth_A': 69.97708999421646, 'Hjorth_M': 0.6693761969836118, 'Hjorth_C': 0.838405013510411}
{'_id': ObjectId('60c90cb9d64ad446fc903d0f'), 't': '2021-06-15 16:25:29.443948', 'complex_wavelet_matrix': 77953988.03

{'_id': ObjectId('60c90d4fd64ad446fc90c9b2'), 't': '2021-06-15 16:27:59.180502', 'complex_wavelet_matrix': 88488730.7151005, 'Hjorth_A': 94.32299666341594, 'Hjorth_M': 1.045823539832839, 'Hjorth_C': 1.4271058970152963}
{'_id': ObjectId('60c90d4fd64ad446fc90c9cd'), 't': '2021-06-15 16:27:59.285799', 'complex_wavelet_matrix': 82342856.81405573, 'Hjorth_A': 93.3179509754717, 'Hjorth_M': 1.0448770787589996, 'Hjorth_C': 1.4578145681811778}
{'_id': ObjectId('60c90d4fd64ad446fc90c9ce'), 't': '2021-06-15 16:27:59.301349', 'complex_wavelet_matrix': 82342856.81405573, 'Hjorth_A': 93.3179509754717, 'Hjorth_M': 1.0448770787589996, 'Hjorth_C': 1.4578145681811778}
{'_id': ObjectId('60c90d4fd64ad446fc90c9d4'), 't': '2021-06-15 16:27:59.332876', 'complex_wavelet_matrix': 79749747.85801446, 'Hjorth_A': 91.07191797166007, 'Hjorth_M': 1.044318963230183, 'Hjorth_C': 1.465140041924614}
{'_id': ObjectId('60c90d4fd64ad446fc90c9f6'), 't': '2021-06-15 16:27:59.442824', 'complex_wavelet_matrix': 81379110.110606

{'_id': ObjectId('60c90db4d64ad430c0da9429'), 't': '2021-06-15 16:29:40.140302', 'complex_wavelet_matrix': 82388910.8192478, 'Hjorth_A': 243.55293781975487, 'Hjorth_M': 0.8498300358320555, 'Hjorth_C': 1.1175157857316578}
{'_id': ObjectId('60c90db4d64ad430c0da942a'), 't': '2021-06-15 16:29:40.390321', 'complex_wavelet_matrix': 84871732.418568, 'Hjorth_A': 237.51595543102218, 'Hjorth_M': 0.873760568832436, 'Hjorth_C': 1.1225786136363574}
{'_id': ObjectId('60c90db4d64ad430c0da942b'), 't': '2021-06-15 16:29:40.528330', 'complex_wavelet_matrix': 84871732.418568, 'Hjorth_A': 237.51595543102218, 'Hjorth_M': 0.873760568832436, 'Hjorth_C': 1.1225786136363574}
{'_id': ObjectId('60c90db4d64ad430c0da9443'), 't': '2021-06-15 16:29:40.719348', 'complex_wavelet_matrix': 73678755.27709241, 'Hjorth_A': 218.76311977277666, 'Hjorth_M': 0.9096339611414647, 'Hjorth_C': 1.1949085818508105}
{'_id': ObjectId('60c90db4d64ad430c0da946f'), 't': '2021-06-15 16:29:40.833355', 'complex_wavelet_matrix': 79764706.933

{'_id': ObjectId('60c90de6d64ad430c0dac6e4'), 't': '2021-06-15 16:30:30.147984', 'complex_wavelet_matrix': 88152337.97543831, 'Hjorth_A': 113.80568341232261, 'Hjorth_M': 0.6048926689795577, 'Hjorth_C': 0.8022252891941282}
{'_id': ObjectId('60c90de6d64ad430c0dac6e6'), 't': '2021-06-15 16:30:30.148985', 'complex_wavelet_matrix': 88152337.97543831, 'Hjorth_A': 113.80568341232261, 'Hjorth_M': 0.6048926689795577, 'Hjorth_C': 0.8022252891941282}
{'_id': ObjectId('60c90de6d64ad430c0dac6e7'), 't': '2021-06-15 16:30:30.148985', 'complex_wavelet_matrix': 88152337.97543831, 'Hjorth_A': 113.80568341232261, 'Hjorth_M': 0.6048926689795577, 'Hjorth_C': 0.8022252891941282}
{'_id': ObjectId('60c90de6d64ad430c0dac72b'), 't': '2021-06-15 16:30:30.409468', 'complex_wavelet_matrix': 91456580.53858328, 'Hjorth_A': 156.72581409593838, 'Hjorth_M': 0.5292375408999384, 'Hjorth_C': 0.6693166534669663}
{'_id': ObjectId('60c90de6d64ad430c0dac72c'), 't': '2021-06-15 16:30:30.410466', 'complex_wavelet_matrix': 91456

...

{'_id': ObjectId('60c92419d64ad446dcc67aeb'), 't': '2021-06-15 18:05:13.476312', 'complex_wavelet_matrix': 92664329.33393162, 'Hjorth_A': 185.24200215937122, 'Hjorth_M': 0.3607831924376306, 'Hjorth_C': 0.481933544171591}
{'_id': ObjectId('60c92419d64ad446dcc67b14'), 't': '2021-06-15 18:05:13.603323', 'complex_wavelet_matrix': 88328954.69139545, 'Hjorth_A': 73.99550282942474, 'Hjorth_M': 0.5415845655093418, 'Hjorth_C': 0.7369693146693045}
{'_id': ObjectId('60c92419d64ad446dcc67b37'), 't': '2021-06-15 18:05:13.744331', 'complex_wavelet_matrix': 80750723.56992926, 'Hjorth_A': 44.54027014423756, 'Hjorth_M': 0.6346925110032469, 'Hjorth_C': 0.8620178620761502}
{'_id': ObjectId('60c92419d64ad446dcc67b6b'), 't': '2021-06-15 18:05:13.902821', 'complex_wavelet_matrix': 82807884.86292447, 'Hjorth_A': 17.829460814194924, 'Hjorth_M': 0.8786345009113896, 'Hjorth_C': 1.2445582582994072}
{'_id': ObjectId('60c9241ad64ad446dcc67b7c'), 't': '2021-06-15 18:05:14.017549', 'complex_wavelet_matrix': 81622701

{'_id': ObjectId('60c9254bd64ad43a1485c18d'), 't': '2021-06-15 18:10:19.220923', 'complex_wavelet_matrix': 78498164.56037338, 'Hjorth_A': 148.35410162210115, 'Hjorth_M': 0.6793595835703153, 'Hjorth_C': 0.9136937896014031}
{'_id': ObjectId('60c9254bd64ad43a1485c1ac'), 't': '2021-06-15 18:10:19.356932', 'complex_wavelet_matrix': 76878053.32734594, 'Hjorth_A': 287.9991848719668, 'Hjorth_M': 0.4633340848485977, 'Hjorth_C': 0.6201262358073327}
{'_id': ObjectId('60c9254bd64ad43a1485c1d1'), 't': '2021-06-15 18:10:19.468938', 'complex_wavelet_matrix': 75647610.43587606, 'Hjorth_A': 164.79423862856515, 'Hjorth_M': 0.7305086586805893, 'Hjorth_C': 1.025114165120669}
{'_id': ObjectId('60c9254bd64ad43a1485c1e5'), 't': '2021-06-15 18:10:19.581947', 'complex_wavelet_matrix': 83157510.9695988, 'Hjorth_A': 198.48259579975218, 'Hjorth_M': 0.6494542031660415, 'Hjorth_C': 0.9026805098520876}
{'_id': ObjectId('60c9254bd64ad43a1485c215'), 't': '2021-06-15 18:10:19.693957', 'complex_wavelet_matrix': 79994800

{'_id': ObjectId('60c926f9d64ad40ec444f475'), 't': '2021-06-15 18:17:29.836347', 'complex_wavelet_matrix': 75963975.41608915, 'Hjorth_A': 146.84828443358455, 'Hjorth_M': 0.9095569109290417, 'Hjorth_C': 1.2808075779696395}
{'_id': ObjectId('60c926f9d64ad40ec444f49c'), 't': '2021-06-15 18:17:29.953356', 'complex_wavelet_matrix': 84626185.947354, 'Hjorth_A': 181.39802973411142, 'Hjorth_M': 0.7200721364868852, 'Hjorth_C': 1.0250118027209136}
{'_id': ObjectId('60c926fad64ad40ec444f4b8'), 't': '2021-06-15 18:17:30.065365', 'complex_wavelet_matrix': 85187000.17626348, 'Hjorth_A': 110.49551944156019, 'Hjorth_M': 0.7594085058709416, 'Hjorth_C': 1.0368324153074462}
{'_id': ObjectId('60c926fad64ad40ec444f4de'), 't': '2021-06-15 18:17:30.185374', 'complex_wavelet_matrix': 78949859.13773221, 'Hjorth_A': 120.17667871680486, 'Hjorth_M': 0.718558445459709, 'Hjorth_C': 0.9614580091987507}
{'_id': ObjectId('60c926fad64ad40ec444f4fc'), 't': '2021-06-15 18:17:30.299385', 'complex_wavelet_matrix': 81478666

{'_id': ObjectId('60ca49e9d64ad44bdca145bb'), 't': '2021-06-16 14:58:49.165286', 'complex_wavelet_matrix': 90540603.58640727, 'Hjorth_A': 686.7490055730834, 'Hjorth_M': 1.0869886790493097, 'Hjorth_C': 1.4647172913541755}
{'_id': ObjectId('60ca49e9d64ad44bdca145d4'), 't': '2021-06-16 14:58:49.279701', 'complex_wavelet_matrix': 81159531.02237697, 'Hjorth_A': 640.3933521648519, 'Hjorth_M': 1.1232257792934708, 'Hjorth_C': 1.5301841314047127}
{'_id': ObjectId('60ca49e9d64ad44bdca14600'), 't': '2021-06-16 14:58:49.404901', 'complex_wavelet_matrix': 80409280.832111, 'Hjorth_A': 390.3822803272422, 'Hjorth_M': 1.290764453925304, 'Hjorth_C': 1.7638973016012087}
{'_id': ObjectId('60ca49e9d64ad44bdca14635'), 't': '2021-06-16 14:58:49.529151', 'complex_wavelet_matrix': 76611093.27415502, 'Hjorth_A': 308.66564715189344, 'Hjorth_M': 1.2179807089686192, 'Hjorth_C': 1.6818620282434888}
{'_id': ObjectId('60ca49e9d64ad44bdca14639'), 't': '2021-06-16 14:58:49.657927', 'complex_wavelet_matrix': 76611093.27

{'_id': ObjectId('60ca55afd64ad42c58b8ce78'), 't': '2021-06-16 15:49:03.874668', 'complex_wavelet_matrix': 82945894.9542813, 'Hjorth_A': 1338.8765220052003, 'Hjorth_M': 0.38030929054209633, 'Hjorth_C': 0.41603391749976454}
{'_id': ObjectId('60ca55b0d64ad42c58b8ce90'), 't': '2021-06-16 15:49:04.017409', 'complex_wavelet_matrix': 71043508.4297033, 'Hjorth_A': 5283.50776419619, 'Hjorth_M': 0.19950622431812326, 'Hjorth_C': 0.2118370836752197}
{'_id': ObjectId('60ca55b0d64ad42c58b8cec4'), 't': '2021-06-16 15:49:04.150827', 'complex_wavelet_matrix': 56683663.07900962, 'Hjorth_A': 11997.510199141125, 'Hjorth_M': 0.19717412020649744, 'Hjorth_C': 0.21004621592871325}
{'_id': ObjectId('60ca55b0d64ad42c58b8cee9'), 't': '2021-06-16 15:49:04.277900', 'complex_wavelet_matrix': 71001814.61886705, 'Hjorth_A': 3175.6685294840518, 'Hjorth_M': 0.29172353478100005, 'Hjorth_C': 0.2963394129404285}
{'_id': ObjectId('60ca55b0d64ad42c58b8cf16'), 't': '2021-06-16 15:49:04.431626', 'complex_wavelet_matrix': 987

In [5]:
import datetime
x = datetime.datetime.now()
print(x)
print(x + datetime.timedelta(seconds=1))

2021-06-16 14:39:18.540740
2021-06-16 14:39:19.540740


In [7]:
print(x - (x - datetime.timedelta(seconds=1)))

0:00:01


In [ ]:
cmw = lambda t, f, s: (1/np.sqrt(s*np.sqrt(np.pi))) * np.exp(-t**2/(2*s**2)) * np.exp(1j*2*np.pi*f*t)

# np.exp(1j*x) = np.cos(x) + 1j*np.sin(x)    #Euler's formula
# x = 2*np.pi*f*t
# (1/np.sqrt(s*np.sqrt(np.pi))) * np.exp(-t**2/(2*s**2)) * np.exp(1j*x) =
# (1/np.sqrt(s*np.sqrt(np.pi))) * np.exp(-t**2/(2*s**2)) * (np.cos(x) + 1j*np.sin(x)) =

# (1/np.sqrt(s*np.sqrt(np.pi))) * np.exp(-t**2/(2*s**2)) * (np.cos(x))       # real term
#+(1/np.sqrt(s*np.sqrt(np.pi))) * np.exp(-t**2/(2*s**2)) * (1j*np.sin(x))    # imaginary term

# (1/np.sqrt(s*np.sqrt(np.pi))) * np.exp(-t**2/(2*s**2)) * (np.cos(2*np.pi*f*t))       # real term
#+1j* (1/np.sqrt(s*np.sqrt(np.pi))) * np.exp(-t**2/(2*s**2)) * (np.sin(2*np.pi*f*t))   # imaginary term





# June 18 - Iteration 3

In [1]:
# Thread 0 (master thread)

%matplotlib widget

from time import time, sleep
from threading import *

import numpy as np
import matplotlib
matplotlib.rcParams['font.size'] = 11
import matplotlib.pyplot as plt
import pandas as pd
import pymongo

client = pymongo.MongoClient()
db = client.test_database
#db.list_collection_names

import ipywidgets
import datetime





# Complex morlet wavelets (cmw) consist of a sine wave multiplied by a Gaussian. 
# (The imaginary term comes from Euler's formula.)
cmw = lambda t, f, s: (1/np.sqrt(s*np.sqrt(np.pi))) * np.exp(-t**2/(2*s**2)) * np.exp(1j*2*np.pi*f*t)
# Where t is time axis, f is peak frequency of wavelet, and s is standard deviation of Gaussian (std_for_gaussian)
std_for_gaussian = lambda n, f: n/(2*np.pi*f)
# Where f is peak frequency of wavelet and n is number of wavelet cycles
wavelet_x = np.linspace(-.25/2, .25/2, 65)
complex_morlet_wavelet = cmw(wavelet_x, f=10, s=std_for_gaussian(n=10, f=10))



def eeg_handler(address: str,*args):
            dateTimeObj = datetime.datetime.now()
            printStr = dateTimeObj.strftime("%Y-%m-%d %H:%M:%S.%f")
            data_dict = {"t":printStr, "TP9":float(args[0]), "AF7":float(args[1]), "AF8":float(args[2]), "TP10":float(args[3])}
            db.raw_cappedCollection_65.insert_one(data_dict)

# Start threads
class EEG_Server(Thread):
    def run(self):
        from pythonosc import dispatcher
        from pythonosc import osc_server
        ip = "192.168.1.165"
        port = 5000

        if __name__ == "__main__":
            dispatcher = dispatcher.Dispatcher()
            dispatcher.map("/muse/eeg", eeg_handler)
            server = osc_server.ThreadingOSCUDPServer((ip, port), dispatcher)
            print("Listening on UDP port "+str(port))
            server.serve_forever()

class Aggregator(Thread):
    def run(self):
        self.running=True
        while self.running==True:
            # Thread 2 (Aggregate capped collection)
            timeit = time()
            docs = db.raw_cappedCollection_65.find({}, projection={"TP9":1, "AF7":1, "AF8":1, "TP10":1, "_id":0})
            X = np.array([[doc['TP9'], doc['AF7'], doc['AF8'], doc['TP10']] for doc in docs])
            wavelet_solution = np.dot(complex_morlet_wavelet, X)   # Convolution-like operation. Shape=(n_wavelets, n_channels)
            wavelet_solution = np.abs(wavelet_solution**2)
            #print("wavelet_solution.shape",wavelet_solution.shape)
            Hjorth_parameters = {'A': np.var(X, axis=0), 
                                 'M': np.sqrt(np.var(np.diff(X, axis=0), axis=0)/np.var(X, axis=0)),
                                 'C': np.sqrt(np.var(np.diff(X, n=2, axis=0), axis=0)/np.var(X, axis=0))}

            #list_wavelet_solutions.append(wavelet_solution)
            #list_Hjorth_parameters.append(Hjorth_parameters)
            
            dateTimeObj2 = datetime.datetime.now()
            global timeStr
            timeStr = dateTimeObj2.strftime("%Y-%m-%d %H:%M:%S.%f")

            processed_data_dict0 = {'t':timeStr, 
                                  'complex_wavelet_matrix':wavelet_solution[0], 
                                  'Hjorth_A':Hjorth_parameters['A'][0],
                                  'Hjorth_M':Hjorth_parameters['M'][0],
                                  'Hjorth_C':Hjorth_parameters['C'][0]}  
            processed_data_dict1 = {'t':timeStr, 
                                  'complex_wavelet_matrix':wavelet_solution[1], 
                                  'Hjorth_A':Hjorth_parameters['A'][1],
                                  'Hjorth_M':Hjorth_parameters['M'][1],
                                  'Hjorth_C':Hjorth_parameters['C'][1]} 
            processed_data_dict2 = {'t':timeStr, 
                                  'complex_wavelet_matrix':wavelet_solution[2], 
                                  'Hjorth_A':Hjorth_parameters['A'][2],
                                  'Hjorth_M':Hjorth_parameters['M'][2],
                                  'Hjorth_C':Hjorth_parameters['C'][2]} 
            processed_data_dict3 = {'t':timeStr, 
                                  'complex_wavelet_matrix':wavelet_solution[3], 
                                  'Hjorth_A':Hjorth_parameters['A'][3],
                                  'Hjorth_M':Hjorth_parameters['M'][3],
                                  'Hjorth_C':Hjorth_parameters['C'][3]} 

            db.processed_0.insert_one(processed_data_dict0)
            db.processed_1.insert_one(processed_data_dict1)
            db.processed_2.insert_one(processed_data_dict2)
            db.processed_3.insert_one(processed_data_dict3)
            db.temp0.insert_one(processed_data_dict0)
            db.temp1.insert_one(processed_data_dict1)
            db.temp2.insert_one(processed_data_dict2)
            db.temp3.insert_one(processed_data_dict3)
            
            
            sleep(0.1)

class Plotter(Thread):
    """Input from MongoDB Collection = db.temp0 and db.temp1 and db.temp2 and db.temp3"""
    def run(self):
        self.running=True
        while self.running==True:
            timeit = time()
            for lines, collection, x_adjust in zip([lines0, lines1, lines2, lines3], 
                                         ['temp0', 'temp1', 'temp2', 'temp3'], [-0.15, -0.05, 0.05, 0.15]):
                change = db[collection].find_one()
                lines[0].set_data(x+x_adjust, [np.sqrt(change['complex_wavelet_matrix']), 
                                               change['Hjorth_A'], change['Hjorth_M'], change['Hjorth_C']])
            fig.canvas.draw()
            fig.canvas.flush_events()
            sleep(0.1)
            
class Experiment_Handler(Thread):
    """Output to MongoDB Collection = db.experiment_timestamps"""
    def __init__(self, textarea_value):
        self.textarea_value = textarea_value
    def run(self):
        self.running=True
        while self.running==True:
            exp_id = self.textarea_value.split(')')[0]
            items_from_param_dict = self.textarea_value.split(')')[1].split(',')
            seconds_from_param_dict = [int(item.split(':')[0]) for item in items_from_param_dict]
            names_from_param_dict = [str(item.split(':')[1]) for item in items_from_param_dict]
            self.time0 = datetime.datetime.now()
            self.previous_second = datetime.timedelta(seconds=0)
            for second, name in zip(seconds_from_param_dict, names_from_param_dict):
                time_nextState = self.time0 + datetime.timedelta(seconds=second)
                
                while datetime.datetime.now() < time_nextState:
                    sleep(0.1)
                    self.current_second = datetime.datetime.now() - self.time0
                    if (self.current_second - self.previous_second) > datetime.timedelta(seconds=1):
                        with output2:
                            print(self.current_second)
                            self.previous_second = self.current_second
                db.experiment_timestamps.insert_one({'t':time_nextState, 'new_state': name, 'experiment_id':exp_id})
            self.running=False
                
            ####################################
            
plt.ioff()

#from IPython.display import display
button = ipywidgets.Button(description="Quit")
output = ipywidgets.Output()
output2 = ipywidgets.Output()


def on_button_clicked(b):
    with output:
        print("Quit button clicked")
        t2.running = False
        t3.running = False

button.on_click(on_button_clicked)

button.layout.margin = '0px 40% 0px 40%'
button.layout.width = '20%'



#display(button, output)




fig = plt.figure(figsize=[10,4])
fig.canvas.header_visible = False
fig.canvas.layout.min_height = '400px'
plt.title('Plotting features')
x = np.array([0,1,2,3])
lines0 = plt.plot(x-0.15, [1,1,1,1], marker='x', ls='')
lines1 = plt.plot(x-0.05, [1,1,1,1], marker='x', ls='')
lines2 = plt.plot(x+0.05, [1,1,1,1], marker='x', ls='')
lines3 = plt.plot(x+0.15, [1,1,1,1], marker='x', ls='')
plt.xticks(ticks=[0,1,2,3], labels=['10Hz wavelet', 'Hjorth_A', 'Hjorth_M', 'Hjorth_C'])
plt.yscale('log')
plt.ylim(0.01, 100000)
plt.xlim(-0.5, 3.5)
plt.legend(['tp9', 'af7', 'af8', 'tp10'], loc='upper right')


# Experimental framework
exp_params_textarea = ipywidgets.Textarea(
    value='',
    placeholder='EXP_ID)integer:\"string\", integer:\"string\", ...:...',
    description='Experiment protocol - {seconds:new_state,}'
    )
exec_button = ipywidgets.Button(description="Begin")

def exec_button_clicked(b):
    """Begin experiment according to parameter dictionary"""
    with output2:
        t4 = Experiment_Handler(textarea_value=exp_params_textarea.value)
        t4.run()
        sleep(0.1)
        while t4.running==True:
            print(datetime.datetime.now() - t4.time0)
            sleep(1)
        print('EXPERIMENT COMPLETE')

exec_button.on_click(exec_button_clicked)

TwoByTwoFooter = ipywidgets.TwoByTwoLayout(top_left=exp_params_textarea, 
                          top_right=exec_button, bottom_left=output, bottom_right=output2)


t1 = EEG_Server()
t2 = Aggregator()
t3 = Plotter()

t1.start()
sleep(0.25)
t2.start()
sleep(0.05)
t3.start()

ipywidgets.AppLayout(
    center=fig.canvas,
    header=button,
    footer=TwoByTwoFooter,
    pane_heights=[1, 10, 10],
)

# ideas - 
# Experimental framework must assign... timestamps (datetime), 
# experiment segment labels (dictionary?) [segment int label with text to display]
# Experiment ID

# retrieve collection aggregated data according to timestamps
# automatically plot and do crude statistics

Listening on UDP port 5000


AppLayout(children=(Button(description='Quit', layout=Layout(grid_area='header', margin='0px 40% 0px 40%', wid…